In [3]:
from python_opensky import OpenSky
from aiohttp import BasicAuth

user = 'jamilvilela'
password = '9!jT9_kFmXGVH!B'

# Initialize API and authenticate
api = OpenSky()
auth = BasicAuth(user, password)
api.authenticate(auth)

# Use await directly in notebook
s = await api.get_states()


C:\Users\jamli\AppData\Local\Temp\ipykernel_11980\628314823.py:10: RuntimeWarning: coroutine 'OpenSky.authenticate' was never awaited
  api.authenticate(auth)


In [4]:
import json
from dataclasses import asdict
from datetime import datetime

def convert_states_response_to_json(states_response):
    """
    Converte um objeto StatesResponse em uma estrutura JSON.
    
    Args:
        states_response: Objeto StatesResponse do python_opensky
        
    Returns:
        dict: Estrutura JSON com os dados dos voos
    """
    json_data = {
        "timestamp": datetime.now().isoformat(),
        "total_states": len(states_response.states) if states_response.states else 0,
        "states": []
    }
    
    if states_response.states:
        for state in states_response.states:
            state_dict = {
                "icao24": state.icao24,
                "callsign": state.callsign.strip() if state.callsign else None,
                "origin_country": state.origin_country,
                "time_position": state.time_position,
                "last_contact": state.last_contact,
                "longitude": state.longitude,
                "latitude": state.latitude,
                "geo_altitude": state.geo_altitude,
                "on_ground": state.on_ground,
                "velocity": state.velocity,
                "true_track": state.true_track,
                "vertical_rate": state.vertical_rate,
                "barometric_altitude": state.barometric_altitude,
                "transponder_code": state.transponder_code,
                "special_purpose_indicator": state.special_purpose_indicator,
                "position_source": str(state.position_source),
                "category": str(state.category)
            }
            json_data["states"].append(state_dict)
    
    return json_data


In [5]:

# Teste com os dados obtidos
json_resultado = convert_states_response_to_json(s)
print(json.dumps(json_resultado, indent=2))

{
  "timestamp": "2026-01-17T23:47:11.572318",
  "total_states": 5281,
  "states": [
    {
      "icao24": "e49406",
      "callsign": null,
      "origin_country": "Brazil",
      "time_position": 1768704403,
      "last_contact": 1768704403,
      "longitude": -44.8466,
      "latitude": -17.0612,
      "geo_altitude": 11925.3,
      "on_ground": false,
      "velocity": 252.61,
      "true_track": 26.62,
      "vertical_rate": 0,
      "barometric_altitude": 11277.6,
      "transponder_code": null,
      "special_purpose_indicator": false,
      "position_source": "PositionSource.ADSB",
      "category": "AircraftCategory.NO_INFORMATION"
    },
    {
      "icao24": "3c4048",
      "callsign": "FMG",
      "origin_country": "Germany",
      "time_position": 1768704352,
      "last_contact": 1768704352,
      "longitude": 13.5015,
      "latitude": 52.3714,
      "geo_altitude": null,
      "on_ground": true,
      "velocity": 11.83,
      "true_track": 247.5,
      "vertical_rate": 

In [ ]:
import boto3

def send_state_to_kinesis(state_dict, stream_name):
    """
    Sends a single state vector to a Kinesis data stream.
    
    Args:
        state_dict (dict): A state vector dictionary
        stream_name (str): Name of the Kinesis stream
    """
    kinesis_client = boto3.client('kinesis')
    
    try:
        response = kinesis_client.put_record(
            StreamName=stream_name,
            Data=json.dumps(state_dict),
            PartitionKey=state_dict['icao24']  # Use ICAO24 as partition key
        )
        return response
    except Exception as e:
        print(f"Error sending state to Kinesis: {e}")
        return None


def send_states_to_kinesis(json_resultado, stream_name):
    """
    Sends all state vectors from json_resultado to Kinesis stream.
    
    Args:
        json_resultado (dict): Output from convert_states_response_to_json()
        stream_name (str): Name of the Kinesis stream
    """
    for state in json_resultado['states']:
        send_state_to_kinesis(state, stream_name)
    print(f"Sent {json_resultado['total_states']} states to Kinesis stream '{stream_name}'")

In [ ]:
classopensky_api.StateVector(arr)¶
Represents the state of a vehicle at a particular time. It has the following fields:

icao24: str - ICAO24 address of the transmitter in hex string representation.
callsign: str - callsign of the vehicle. Can be None if no callsign has been received.
origin_country: str - inferred through the ICAO24 address.
time_position: int - seconds since epoch of last position report. Can be None if there was no position report received by OpenSky within 15s before.
last_contact: int - seconds since epoch of last received message from this transponder.
longitude: float - in ellipsoidal coordinates (WGS-84) and degrees. Can be None.
latitude: float - in ellipsoidal coordinates (WGS-84) and degrees. Can be None.
geo_altitude: float - geometric altitude in meters. Can be None.
on_ground: bool - true if aircraft is on ground (sends ADS-B surface position reports).
velocity: float - over ground in m/s. Can be None if information not present.
true_track: float - in decimal degrees (0 is north). Can be None if information not present.
vertical_rate: float - in m/s, incline is positive, decline negative. Can be None if information not present.
sensors: list [int] - serial numbers of sensors which received messages from the vehicle within the validity period of this state vector. Can be None if no filtering for sensor has been requested.
baro_altitude: float - barometric altitude in meters. Can be None.
squawk: str - transponder code aka Squawk. Can be None.
spi: bool - special purpose indicator.
position_source: int - origin of this state’s position: 0 = ADS-B, 1 = ASTERIX, 2 = MLAT, 3 = FLARM
category: int - aircraft category: 0 = No information at all, 1 = No ADS-B Emitter Category Information, 2 = Light (< 15500 lbs), 3 = Small (15500 to 75000 lbs), 4 = Large (75000 to 300000 lbs), 5 = High Vortex Large (aircraft such as B-757), 6 = Heavy (> 300000 lbs), 7 = High Performance (> 5g acceleration and 400 kts), 8 = Rotorcraft, 9 = Glider / sailplane, 10 = Lighter-than-air, 11 = Parachutist / Skydiver, 12 = Ultralight / hang-glider / paraglider, 13 = Reserved, 14 = Unmanned Aerial Vehicle, 15 = Space / Trans-atmospheric vehicle, 16 = Surface Vehicle – Emergency Vehicle, 17 = Surface Vehicle – Service Vehicle, 18 = Point Obstacle (includes tethered balloons), 19 = Cluster Obstacle, 20 = Line Obstacle.
